In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [2]:
writer = SummaryWriter()

In [3]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [4]:
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14393, 4096) (14393, 1) (3599, 4096) (3599, 1)


In [5]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [6]:
train_set = train_set.reshape((-1,64,64))
test_set = test_set.reshape((-1,64,64))
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392, 1) (3598, 64, 64) (3598, 1)


In [7]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)

print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [8]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [9]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [10]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [11]:
class SleepStagerBlanco2020(nn.Module):
    """Sleep staging architecture from Blanco et al 2020.

    Convolutional neural network for sleep staging described in [Blanco2020]_.
    A series of seven convolutional layers with kernel sizes running down from 7 to 3,
    in an attempt to extract more general features at the beginning, while more specific
    and complex features were extracted in the final stages.

    Parameters
    ----------
    n_channels : int
        Number of EEG channels.
    sfreq : float
        EEG sampling frequency.
    n_conv_chans : int
        Number of convolutional channels. Set to 20 in [Blanco2020]_.
    n_groups : int
        Number of groups for the convolution. Set to 2 in [Blanco2020]_ for 2 Channel EEG.
        controls the connections between inputs and outputs. n_channels and n_conv_chans must be
        divisible by n_groups.
    input_size_s : float
        Size of the input, in seconds.
    n_classes : int
        Number of classes.
    dropout : float
        Dropout rate before the output dense layer.
    apply_batch_norm : bool
        If True, apply batch normalization after both temporal convolutional
        layers.
    return_feats : bool
        If True, return the features, i.e. the output of the feature extractor
        (before the final linear layer). If False, pass the features through
        the final linear layer.

    References
    ----------
    .. [Blanco2020] Fernandez-Blanco, E., Rivero, D. & Pazos, A. Convolutional
        neural networks for sleep stage scoring on a two-channel EEG signal.
        Soft Comput 24, 4067–4079 (2020). https://doi.org/10.1007/s00500-019-04174-1
    """

    def __init__(self, n_channels=64, sfreq=160, n_conv_chans=20, input_size_s=0.4,
                 n_classes=4, n_groups=2, max_pool_size=2, dropout=0.5, apply_batch_norm=False,
                 return_feats=False):
        super().__init__()


        self.n_channels = n_channels

        batch_norm = nn.BatchNorm2d if apply_batch_norm else nn.Identity

        self.feature_extractor = nn.Sequential(
            # b 64 64
            nn.Conv2d(n_channels, n_conv_chans, (1, 7), groups=n_groups, padding=0),
            # b 20 58
            batch_norm(n_conv_chans),
            nn.ReLU(),
            nn.MaxPool2d((1, max_pool_size)),
            #b 20 29
            nn.Conv2d(n_conv_chans, n_conv_chans, (1, 5), groups=n_conv_chans, padding=0),
            #b 20 25
            batch_norm(n_conv_chans),
            nn.ReLU(),
            nn.MaxPool2d((1, max_pool_size)),
            #b 20 12
            nn.Conv2d(n_conv_chans, n_conv_chans, (1, 3), groups=n_conv_chans, padding=0),
            #b 20 10
            batch_norm(n_conv_chans),
            nn.ReLU(),
            nn.MaxPool2d((1, max_pool_size)),
            #b 20 5
            nn.Flatten(),
            nn.Dropout(dropout),
            nn.Linear(100, n_classes)
        )

    def forward(self, x):
        """Forward pass.
        Parameters
        ----------
        x: torch.Tensor
            Batch of EEG windows of shape (batch_size, n_channels, n_times).
        """
        if x.ndim == 3:
            x = x.unsqueeze(2)
        
        return self.feature_extractor(x)

In [12]:
model = SleepStagerBlanco2020()
a = torch.randn((64,64,1,64))
b = model(a)
b.shape

torch.Size([64, 4])

In [13]:
model = SleepStagerBlanco2020().to(device)

In [14]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [15]:

# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)


        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)

        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])

        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])

        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))


        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        
        

Epoch [1/300], Step [1/225], Training Accuracy: 25.0000%, Training Loss: 1.4064%
Epoch [1/300], Step [2/225], Training Accuracy: 24.2188%, Training Loss: 1.4027%
Epoch [1/300], Step [3/225], Training Accuracy: 22.9167%, Training Loss: 1.4054%
Epoch [1/300], Step [4/225], Training Accuracy: 24.6094%, Training Loss: 1.4094%
Epoch [1/300], Step [5/225], Training Accuracy: 23.4375%, Training Loss: 1.4091%
Epoch [1/300], Step [6/225], Training Accuracy: 24.2188%, Training Loss: 1.4065%
Epoch [1/300], Step [7/225], Training Accuracy: 25.0000%, Training Loss: 1.4084%
Epoch [1/300], Step [8/225], Training Accuracy: 25.5859%, Training Loss: 1.4055%
Epoch [1/300], Step [9/225], Training Accuracy: 24.3056%, Training Loss: 1.4089%
Epoch [1/300], Step [10/225], Training Accuracy: 24.3750%, Training Loss: 1.4098%
Epoch [1/300], Step [11/225], Training Accuracy: 24.2898%, Training Loss: 1.4093%
Epoch [1/300], Step [12/225], Training Accuracy: 24.8698%, Training Loss: 1.4064%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [107/225], Training Accuracy: 25.2336%, Training Loss: 1.3986%
Epoch [1/300], Step [108/225], Training Accuracy: 25.1736%, Training Loss: 1.3986%
Epoch [1/300], Step [109/225], Training Accuracy: 25.2294%, Training Loss: 1.3985%
Epoch [1/300], Step [110/225], Training Accuracy: 25.3267%, Training Loss: 1.3983%
Epoch [1/300], Step [111/225], Training Accuracy: 25.3378%, Training Loss: 1.3981%
Epoch [1/300], Step [112/225], Training Accuracy: 25.3348%, Training Loss: 1.3980%
Epoch [1/300], Step [113/225], Training Accuracy: 25.2351%, Training Loss: 1.3981%
Epoch [1/300], Step [114/225], Training Accuracy: 25.3152%, Training Loss: 1.3979%
Epoch [1/300], Step [115/225], Training Accuracy: 25.3804%, Training Loss: 1.3977%
Epoch [1/300], Step [116/225], Training Accuracy: 25.3637%, Training Loss: 1.3976%
Epoch [1/300], Step [117/225], Training Accuracy: 25.4274%, Training Loss: 1.3975%
Epoch [1/300], Step [118/225], Training Accuracy: 25.3840%, Training Loss: 1.3976%
Epoc

Epoch [1/300], Step [219/225], Training Accuracy: 25.7135%, Training Loss: 1.3928%
Epoch [1/300], Step [220/225], Training Accuracy: 25.7528%, Training Loss: 1.3927%
Epoch [1/300], Step [221/225], Training Accuracy: 25.6929%, Training Loss: 1.3929%
Epoch [1/300], Step [222/225], Training Accuracy: 25.7179%, Training Loss: 1.3927%
Epoch [1/300], Step [223/225], Training Accuracy: 25.6516%, Training Loss: 1.3929%
Epoch [1/300], Step [224/225], Training Accuracy: 25.6557%, Training Loss: 1.3929%
Epoch [1/300], Step [225/225], Training Accuracy: 25.6531%, Training Loss: 1.3929%
Epoch [2/300], Step [1/225], Training Accuracy: 23.4375%, Training Loss: 1.4073%
Epoch [2/300], Step [2/225], Training Accuracy: 27.3438%, Training Loss: 1.3879%
Epoch [2/300], Step [3/225], Training Accuracy: 26.5625%, Training Loss: 1.3847%
Epoch [2/300], Step [4/225], Training Accuracy: 25.7812%, Training Loss: 1.3864%
Epoch [2/300], Step [5/225], Training Accuracy: 26.5625%, Training Loss: 1.3885%
Epoch [2/300],

Epoch [2/300], Step [132/225], Training Accuracy: 28.6458%, Training Loss: 1.3796%
Epoch [2/300], Step [133/225], Training Accuracy: 28.7242%, Training Loss: 1.3794%
Epoch [2/300], Step [134/225], Training Accuracy: 28.7197%, Training Loss: 1.3793%
Epoch [2/300], Step [135/225], Training Accuracy: 28.7384%, Training Loss: 1.3792%
Epoch [2/300], Step [136/225], Training Accuracy: 28.7339%, Training Loss: 1.3792%
Epoch [2/300], Step [137/225], Training Accuracy: 28.7409%, Training Loss: 1.3792%
Epoch [2/300], Step [138/225], Training Accuracy: 28.6911%, Training Loss: 1.3790%
Epoch [2/300], Step [139/225], Training Accuracy: 28.6084%, Training Loss: 1.3792%
Epoch [2/300], Step [140/225], Training Accuracy: 28.5491%, Training Loss: 1.3793%
Epoch [2/300], Step [141/225], Training Accuracy: 28.5129%, Training Loss: 1.3794%
Epoch [2/300], Step [142/225], Training Accuracy: 28.5431%, Training Loss: 1.3793%
Epoch [2/300], Step [143/225], Training Accuracy: 28.5511%, Training Loss: 1.3791%
Epoc

Epoch [3/300], Step [32/225], Training Accuracy: 31.2012%, Training Loss: 1.3514%
Epoch [3/300], Step [33/225], Training Accuracy: 31.0606%, Training Loss: 1.3517%
Epoch [3/300], Step [34/225], Training Accuracy: 31.2500%, Training Loss: 1.3512%
Epoch [3/300], Step [35/225], Training Accuracy: 31.0268%, Training Loss: 1.3521%
Epoch [3/300], Step [36/225], Training Accuracy: 30.8594%, Training Loss: 1.3522%
Epoch [3/300], Step [37/225], Training Accuracy: 30.8699%, Training Loss: 1.3517%
Epoch [3/300], Step [38/225], Training Accuracy: 30.9622%, Training Loss: 1.3510%
Epoch [3/300], Step [39/225], Training Accuracy: 31.0096%, Training Loss: 1.3504%
Epoch [3/300], Step [40/225], Training Accuracy: 30.9766%, Training Loss: 1.3502%
Epoch [3/300], Step [41/225], Training Accuracy: 30.7546%, Training Loss: 1.3505%
Epoch [3/300], Step [42/225], Training Accuracy: 30.5432%, Training Loss: 1.3517%
Epoch [3/300], Step [43/225], Training Accuracy: 30.3416%, Training Loss: 1.3521%
Epoch [3/300], S

...

Epoch [298/300], Step [133/225], Training Accuracy: 46.8867%, Training Loss: 1.1052%
Epoch [298/300], Step [134/225], Training Accuracy: 46.9683%, Training Loss: 1.1055%
Epoch [298/300], Step [135/225], Training Accuracy: 46.9444%, Training Loss: 1.1056%
Epoch [298/300], Step [136/225], Training Accuracy: 47.0588%, Training Loss: 1.1047%
Epoch [298/300], Step [137/225], Training Accuracy: 47.0233%, Training Loss: 1.1046%
Epoch [298/300], Step [138/225], Training Accuracy: 47.0448%, Training Loss: 1.1044%
Epoch [298/300], Step [139/225], Training Accuracy: 47.0099%, Training Loss: 1.1047%
Epoch [298/300], Step [140/225], Training Accuracy: 46.9643%, Training Loss: 1.1052%
Epoch [298/300], Step [141/225], Training Accuracy: 46.9526%, Training Loss: 1.1049%
Epoch [298/300], Step [142/225], Training Accuracy: 46.9300%, Training Loss: 1.1047%
Epoch [298/300], Step [143/225], Training Accuracy: 46.9078%, Training Loss: 1.1045%
Epoch [298/300], Step [144/225], Training Accuracy: 46.8641%, Tra

Epoch [299/300], Step [40/225], Training Accuracy: 47.7734%, Training Loss: 1.1024%
Epoch [299/300], Step [41/225], Training Accuracy: 47.5991%, Training Loss: 1.1057%
Epoch [299/300], Step [42/225], Training Accuracy: 47.4330%, Training Loss: 1.1054%
Epoch [299/300], Step [43/225], Training Accuracy: 47.2747%, Training Loss: 1.1066%
Epoch [299/300], Step [44/225], Training Accuracy: 47.3722%, Training Loss: 1.1062%
Epoch [299/300], Step [45/225], Training Accuracy: 47.4653%, Training Loss: 1.1070%
Epoch [299/300], Step [46/225], Training Accuracy: 47.5204%, Training Loss: 1.1053%
Epoch [299/300], Step [47/225], Training Accuracy: 47.3404%, Training Loss: 1.1058%
Epoch [299/300], Step [48/225], Training Accuracy: 47.2005%, Training Loss: 1.1053%
Epoch [299/300], Step [49/225], Training Accuracy: 47.0663%, Training Loss: 1.1086%
Epoch [299/300], Step [50/225], Training Accuracy: 47.0312%, Training Loss: 1.1075%
Epoch [299/300], Step [51/225], Training Accuracy: 47.0282%, Training Loss: 

Epoch [299/300], Step [162/225], Training Accuracy: 46.9522%, Training Loss: 1.1033%
Epoch [299/300], Step [163/225], Training Accuracy: 46.9421%, Training Loss: 1.1033%
Epoch [299/300], Step [164/225], Training Accuracy: 46.9417%, Training Loss: 1.1031%
Epoch [299/300], Step [165/225], Training Accuracy: 46.8939%, Training Loss: 1.1034%
Epoch [299/300], Step [166/225], Training Accuracy: 46.8562%, Training Loss: 1.1037%
Epoch [299/300], Step [167/225], Training Accuracy: 46.8656%, Training Loss: 1.1032%
Epoch [299/300], Step [168/225], Training Accuracy: 46.8378%, Training Loss: 1.1032%
Epoch [299/300], Step [169/225], Training Accuracy: 46.8750%, Training Loss: 1.1029%
Epoch [299/300], Step [170/225], Training Accuracy: 46.8015%, Training Loss: 1.1030%
Epoch [299/300], Step [171/225], Training Accuracy: 46.8019%, Training Loss: 1.1029%
Epoch [299/300], Step [172/225], Training Accuracy: 46.7751%, Training Loss: 1.1028%
Epoch [299/300], Step [173/225], Training Accuracy: 46.7847%, Tra

Epoch [300/300], Step [67/225], Training Accuracy: 46.9916%, Training Loss: 1.1057%
Epoch [300/300], Step [68/225], Training Accuracy: 47.0129%, Training Loss: 1.1048%
Epoch [300/300], Step [69/225], Training Accuracy: 46.9429%, Training Loss: 1.1040%
Epoch [300/300], Step [70/225], Training Accuracy: 47.0759%, Training Loss: 1.1036%
Epoch [300/300], Step [71/225], Training Accuracy: 47.0070%, Training Loss: 1.1049%
Epoch [300/300], Step [72/225], Training Accuracy: 46.8967%, Training Loss: 1.1054%
Epoch [300/300], Step [73/225], Training Accuracy: 46.9606%, Training Loss: 1.1065%
Epoch [300/300], Step [74/225], Training Accuracy: 47.0228%, Training Loss: 1.1053%
Epoch [300/300], Step [75/225], Training Accuracy: 47.0417%, Training Loss: 1.1050%
Epoch [300/300], Step [76/225], Training Accuracy: 47.0600%, Training Loss: 1.1054%
Epoch [300/300], Step [77/225], Training Accuracy: 47.0982%, Training Loss: 1.1041%
Epoch [300/300], Step [78/225], Training Accuracy: 47.1354%, Training Loss: 

Epoch [300/300], Step [192/225], Training Accuracy: 46.9645%, Training Loss: 1.1003%
Epoch [300/300], Step [193/225], Training Accuracy: 46.9479%, Training Loss: 1.1003%
Epoch [300/300], Step [194/225], Training Accuracy: 46.9233%, Training Loss: 1.1000%
Epoch [300/300], Step [195/225], Training Accuracy: 46.9311%, Training Loss: 1.1003%
Epoch [300/300], Step [196/225], Training Accuracy: 46.9627%, Training Loss: 1.1002%
Epoch [300/300], Step [197/225], Training Accuracy: 47.0019%, Training Loss: 1.0997%
Epoch [300/300], Step [198/225], Training Accuracy: 47.0644%, Training Loss: 1.0989%
Epoch [300/300], Step [199/225], Training Accuracy: 47.0634%, Training Loss: 1.0988%
Epoch [300/300], Step [200/225], Training Accuracy: 47.0469%, Training Loss: 1.0992%
Epoch [300/300], Step [201/225], Training Accuracy: 47.0616%, Training Loss: 1.0993%
Epoch [300/300], Step [202/225], Training Accuracy: 47.0684%, Training Loss: 1.0996%
Epoch [300/300], Step [203/225], Training Accuracy: 47.0905%, Tra

In [16]:

# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 45.49749861033908 %


In [17]:
#for i in range(10):
#    x = all_data[i]
#    y = all_label[all-i]